In [2]:
import re
import nltk
import numpy as np
import pandas as pd
from langdetect import detect
from sentence_transformers import SentenceTransformer, InputExample, losses
from sentence_transformers.util import semantic_search 
from torch.utils.data import DataLoader
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem import PorterStemmer
from sklearn.preprocessing import MultiLabelBinarizer
import faiss
from FlagEmbedding import FlagReranker
from sklearn.model_selection import train_test_split


/Users/ladka6/Projects/semantic-search/venv/lib/python3.9/site-packages/urllib3/__init__.py:34: NotOpenSSLWarning: urllib3 v2 only supports OpenSSL 1.1.1+, currently the 'ssl' module is compiled with 'LibreSSL 2.8.3'. See: https://github.com/urllib3/urllib3/issues/3020
  warnings.warn(


In [3]:
FILE_PATH = '../data/book_data.csv'

df = pd.read_csv(FILE_PATH)

df = df.dropna(subset=['Title', 'Description', 'Genres'])


In [4]:
def preprocess_text(text):
    text = text.lower()
    text = re.sub(r'[^a-zA-Z\s]', '', text)
    tokens = word_tokenize(text)
    stop_words = set(stopwords.words('english'))
    tokens = [token for token in tokens if token not in stop_words]
    text = ' '.join(tokens)
    return text


In [5]:
# def title_description_genres_to_string(row):
#   genres = ' '.join([genre.strip() for genre in row['Genres'].split(',')])

#   title = row['Title']

#   descriptions = str(row['Description'])

#   tokens = word_tokenize(descriptions)

#   tokens = [word.lower() for word in tokens if word.isalpha()]

#   stop_words = set(stopwords.words('english'))
#   tokens = [word for word in tokens if word not in stop_words]

#   porter = PorterStemmer()
#   tokens = [porter.stem(word) for word in tokens]

#   preprocessed_text = ' '.join(tokens)

#   return "%s %s %s" %(title, genres, preprocessed_text)


In [6]:
# df['Combined'] = df.apply(title_description_genres_to_string, axis=1)
df['Title'] = preprocess_text(df['Title'])
df['Description'] = preprocess_text(df['Description'])
df['Genres'] = preprocess_text(df['Genres'])


Id                                              Title  \
0        1                                            Beowulf   
1        2                        The Evening and the Morning   
2        3                                   The Abbot's Tale   
3        4  Ibn Fadlān and the Land of Darkness: Arab Trav...   
4        5                                   The Empty Throne   
...    ...                                                ...   
1780  1843                             The Soul of an Octopus   
1781  1844  The Jim Corbett Omnibus: "Man-eaters of Kumaon...   
1782  1845  The Tiger: A True Story of Vengeance and Survival   
1783  1846  100 Heartbeats: The Race to Save Earth's Most ...   
1784  1847                          An Elephant in My Kitchen   

                       Author  Rating  \
0               Seamus Heaney    3.48   
1                 Ken Follett    4.38   
2               Conn Iggulden    4.05   
3            Ahmad ibn Fadlān    3.87   
4            Bernard Cornwell    4.38   
...                       ...     ...   
1780            Sy Montgomery    3.93   
1781              Jim Corbett    4.54   
1782            John Vaillant    4.07   
1783              Jeff Corwin    4.17   
1784  Françoise Malby-Anthony    4.39   

                                            Description  \
0     Composed toward the end of the first millenniu...   
1     The thrilling and addictive prequel to The Pil...   
2     In the year 937, the new king of England, a gr...   
3     In 922 AD, an Arab envoy from Baghdad named Ib...   
4     This eighth entry in New York Times bestsellin...   
...                                                 ...   
1780  In pursuit of the wild, solitary, predatory oc...   
1781  Jim Corbett's riveting accounts of shikar in t...   
1782  It’s December 1997, and a man-eating tiger is ...   
1783  It's no secret that our planet―and the delicat...   
1784  A blonde, chic Parisienne, Francoise never exp...   

                                                 Genres  \
0     Classics, Poetry, Fiction, Fantasy, Mythology,...   
1     Historical Fiction, Fiction, Historical, Audio...   
2     Historical Fiction, Fiction, Historical, Medie...   
3     History, Travel, Nonfiction, Classics, Islam, ...   
4     Historical Fiction, Fiction, Historical, Medie...   
...                                                 ...   
1780  Nonfiction, Science, Animals, Nature, Memoir, ...   
1781  Nonfiction, Wildlife, Nature, Travel, Biograph...   
1782  Nonfiction, History, Nature, Animals, Russia, ...   
1783  Nonfiction, Animals, Science, Nature, Conserva...   
1784  Nonfiction, Animals, Memoir, Africa, Nature, B...   

                                                Reviews  \
0     *bum bum* IN A WORLD . . . *bum bum* . . . FUL...   
1     It's 997 CE, the end of the Dark Ages in Engla...   
2     There is never one truth, one love, or one ene...   
3     رسالة ابن فضلان .. أو ما يسمى برحلة ابن فضلان ...   
4     The Empty Throne was an improvement over The P...   
...                                                 ...   
1780  I'm kind of "eh" on this book. It bills itself...   
1781  One of the best books ever written, this book ...   
1782  Fearful symmetry indeed. In 1997, during time ...   
1783  I learned a lot reading this book. Frightening...   
1784  Thula Thula, South Africa, the sanctuary for e...   

                                               Combined  
0     Beowulf Classics Poetry Fiction Fantasy Mythol...  
1     The Evening and the Morning Historical Fiction...  
2     The Abbot's Tale Historical Fiction Fiction Hi...  
3     Ibn Fadlān and the Land of Darkness: Arab Trav...  
4     The Empty Throne Historical Fiction Fiction Hi...  
...                                                 ...  
1780  The Soul of an Octopus Nonfiction Science Anim...  
1781  The Jim Corbett Omnibus: "Man-eaters of Kumaon...  
1782  The Tiger: A True Story of Vengeance and Survi...  
1783  100 Heartbeats: The R

In [8]:
train, valid = train_test_split(df, test_size=0.2, random_state=42)

train_examples = [
    InputExample(texts=[row["Title"], row['Genres'], row['Description']], label=1.0) for _, row in train.iterrows()
]

model = SentenceTransformer("paraphrase-MiniLM-L6-v2")

data_loader = DataLoader(train_examples, shuffle=True, batch_size=32)
train_loss = losses.CosineSimilarityLoss(model=model)

model.fit(train_objectives=[(data_loader, train_loss)], epochs=1)

model.save("out/fine_tuned_sbert_model_test")


Epoch:   0%|          | 0/1 [00:00<?, ?it/s]

Iteration:   0%|          | 0/45 [00:00<?, ?it/s]

In [48]:
documents = list(df['Description'])

sbert_model = SentenceTransformer('out/fine_tuned_sbert_model_test')

document_embeddings = sbert_model.encode(documents, convert_to_tensor=True)

index = faiss.IndexFlatL2(document_embeddings.size(1))

index.add(document_embeddings.cpu().numpy())

faiss.write_index(index, 'vectors/fine_tuned_faiss_index_t.index')


In [53]:
# User
# valid_documents = valid['Description'].tolist()
# results = {}

# for i, query in enumerate(valid_documents):
#     query_embedding = model.encode([query], convert_to_tensor=True)
#     distances, indices = index.search(query_embedding.cpu().numpy(), k=5)
#     top_indices = indices[0]
#     results[i] = top_indices

# def evaluate(results):
#     relevant_count = 0
#     total_queries = len(results)
#     for i, (_, top_indices) in enumerate(results.items()):
#         # Check if any of the top indices match the index of the query document in the validation set
#         if i in top_indices[:1]:
#             relevant_count += 1
#     precision_at_1 = relevant_count / total_queries
#     return precision_at_1


# precision_at_1 = evaluate(results)
# print("Precision@1 on Validation Set:", precision_at_1)

{0: array([1192, 1188,  218,  280,  645]), 1: array([426, 394, 428, 422, 393]), 2: array([1474,   59,  498,  336, 1376]), 3: array([765, 798, 790, 170, 809]), 4: array([ 485,  664, 1311, 1035, 1328]), 5: array([ 479,  729,  466, 1521,  828]), 6: array([ 109,  114,  101,  145, 1660]), 7: array([ 774,  767,  165, 1647,  305]), 8: array([  85, 1431,  907,  879,  910]), 9: array([1188, 1035, 1019, 1114, 1192]), 10: array([1721,  674, 1303,  685,  709]), 11: array([530, 550, 527, 515, 554]), 12: array([984, 975, 450, 452, 449]), 13: array([ 538, 1367, 1645,  534,   59]), 14: array([1057, 1019, 1353, 1039, 1015]), 15: array([ 677, 1319,  664, 1311,  688]), 16: array([1101, 1625, 1068,  764,  664]), 17: array([316, 303, 294, 683, 390]), 18: array([1149, 1157,  862,  711,  351]), 19: array([ 930, 1035, 1019, 1237,  266]), 20: array([ 344,  313, 1285, 1185, 1767]), 21: array([ 590,  391, 1485,  196,   48]), 22: array([948, 952, 916, 943, 755]), 23: array([785, 798, 802, 769, 809]), 24: array([ 

In [49]:
def semantic_search(query, k=5, rerank_k=3, flag_reranker=None, flag_threshold=0):
    
    query_embedding = sbert_model.encode([query], convert_to_tensor=True)
    distances, indices = index.search(query_embedding.cpu().numpy(), k + rerank_k)

    initial_indices = indices[0][:k]

    initial_documents = df.iloc[initial_indices][['Title', 'Description', 'Genres']]
    genres_text = ''.join(initial_documents['Genres'].to_list())

    initial_documents['Text'] = initial_documents['Title'].str.lower() + ' ' + initial_documents['Description'].str.lower() + genres_text  # Concatenate title and description
    initial_distances = distances[0][:k]

    initial_results = list(zip(initial_documents['Title'], initial_documents['Text'], initial_distances))

    if flag_reranker:
        flag_scores = [flag_reranker.compute_score([query, text]) for _, text, _ in initial_results]
        reranked_results = [(title, text, dist + flag_score) for title, text, dist, flag_score in zip(initial_documents['Title'], initial_documents['Text'], initial_distances, flag_scores) if abs(flag_score) > flag_threshold]
        reranked_results = sorted(reranked_results, key=lambda x: x[2], reverse=True)[:rerank_k]
    else:
        reranked_results = initial_results[:rerank_k]

    return reranked_results

print("START")
query = "Search for science fiction books  with a focus on space exploration."
flag_reranker = FlagReranker('BAAI/bge-small-en-v1.5', use_fp16=True)  # Initialize the FlagReranker object
results = semantic_search(query, flag_reranker=flag_reranker)

for rank, (title, text, score) in enumerate(results, start=1):
    print(f"Rank {rank}: {title} (Score: {score})")


START


Some weights of BertForSequenceClassification were not initialized from the model checkpoint at BAAI/bge-small-en-v1.5 and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


[ 152 1363 1372 1373  891]
Rank 1: Starship Troopers (Score: 35.16937255859375)
Rank 2: Gods from Outer Space (Score: 35.109352111816406)
Rank 3: Voodoo Science: The Road from Foolishness to Fraud (Score: 34.12990951538086)
